i need to make sure i am using a good sample of ETFs here. right now the list is too random

In [1]:
mydict = {"EWA": "Australia",
 "EWO": "Austria",
 "EWK": "Belgium",
 "EWZ": "Brazil",
 "EWC": "Canada",
 "ECH": "Chile",
 "GXC": "China",
 "GXG": "Colombia",
 "EGPT": "Egypt",
 "EWQ": "France",
 "EWG": "Germany",
 "EWH": "Hong Kong",
 "PIN": "India",
 "IDX": "Indonesia",
 "EIRL": "Ireland",
 "EIS": "Israel",
 "EWI": "Italy",
 "EWM": "Malaysia",
 "EWW": "Mexico",
 "EWN": "Netherlands",
 "EPU": "Peru",
 "EPOL": "Poland",
 "EWS": "Singapore",
 "EZA": "South Africa",
 "EWY": "South Korea",
 "EWP": "Spain",
 "EWD": "Sweden",
 "EWL": "Switzerland",
 "EWT": "Taiwan",
 "THD": "Thailand",
 "TUR": "Turkey",
 "EWU": "United Kingdom",
 "EUSA": "United States",
 "VNM": "Vietnam",
 "ENZL": "New Zealand",
 "NORW": "Norway",
 "EPHE": "Philippines",
 "PGAL": "Portugal",
 "NGE": "Nigeria",
 "QAT": "Qatar",
 "UAE": "United Arab Emirates",
 "GREK": "Greece",
 "EWJ": "Japan",
 "KSA": "Saudi Arabia",
 "PAK": "Pakistan",
 "ARGT": "Argentina",
 "EDEN": "Denmark",
 "EFNL": "Finland",
 "KWT": "Kuwait"}

countries = ['Australia','Brazil','Canada','Chile','China','Colombia','France','Germany','Hong Kong',
             'India','Indonesia','Japan','Mexico','New Zealand','Norway','Peru','Poland','South Africa',
             'South Korea','Sweden','Switzerland','Taiwan','Turkey','United Kingdom','United States']

inverse_dict = {v: k for k, v in mydict.items()}
ETF_list = [inverse_dict[x] for x in countries]
ETF_list

['EWA',
 'EWZ',
 'EWC',
 'ECH',
 'GXC',
 'GXG',
 'EWQ',
 'EWG',
 'EWH',
 'PIN',
 'IDX',
 'EWJ',
 'EWW',
 'ENZL',
 'NORW',
 'EPU',
 'EPOL',
 'EZA',
 'EWY',
 'EWD',
 'EWL',
 'EWT',
 'TUR',
 'EWU',
 'EUSA']

In [2]:
from ipynb.fs.full.FXpricelist import full_df
from ipynb.fs.full.quick_functions import *
import pandas as pd
import plotly.graph_objects as go
import datetime
from datetime import date
from pandas_datareader import data

years = 5
start_date = datetime.datetime.now() - datetime.timedelta(days=365*years)
end_date = date.today()
fred_data = data.DataReader(ETF_list, 'stooq', start_date, end_date)
final_df = fred_data['Close'].sort_index(ascending=True)
indexed_df = final_df / final_df.iloc[0] * 100
for sector in ETF_list:
    indexed_df[f"{sector} / EUSA"] = indexed_df[sector] / indexed_df["EUSA"] * 100
ratios = [f"{sector} / EUSA" for sector in ETF_list[:-1]]
fig = px.line(indexed_df[ratios])
fig.show()

[*********************100%***********************]  25 of 25 completed


<IPython.core.display.Javascript object>

In [3]:
#indexed_df.to_csv("indexed_df.csv")

# indexed_df = pd.read_csv("indexed_df.csv",index_col=0)
# indexed_df.index = pd.to_datetime(indexed_df.index)
# indexed_df.head()

import pandas as pd
from sklearn.linear_model import Lasso
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
from sklearn.metrics import r2_score
from plotly.subplots import make_subplots

df_fx = 1 / full_df(10,1)
df_fx.tail()

In [32]:
currency = "COP"
test_df = indexed_df[ETF_list].merge(df_fx[currency],left_index=True,right_index=True,how="inner")

y = test_df[currency]
X = test_df[ETF_list].fillna(method="bfill")
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.75, random_state=42)
lasso = Lasso(max_iter=10000,alpha=0.9)
lasso.fit(X_train, y_train)
y_pred = lasso.predict(X_test)
mse = mean_squared_error(y_test, y_pred)

test_df["ypred"] = lasso.predict(test_df[ETF_list].fillna(method="bfill"))
test_df["resids"] = (test_df[currency] - test_df["ypred"]) / test_df[currency] * 100

coefficients = lasso.coef_
r_squared = r2_score(y_test, lasso.predict(X_test))

X_colnames = X.columns
selected_X_vars = []
for i in range(len(coefficients)):
    if coefficients[i] != 0:
        selected_X_vars.append(X_colnames[i])
non_zero_coefficients = [round(x,3) for x in coefficients if x != 0]
xvars = [mydict[x] for x in selected_X_vars]

print(currency)
print("Mean squared error:", round(mse,2))
print("R-squared:", round(r_squared,2))

title = f"R^2: {round(r_squared,2)}"
fig = make_subplots(rows=1, cols=2)
fig.add_scatter(x=test_df.index, y=test_df[currency], mode='lines', name=currency, row=1, col=1)
fig.add_scatter(x=test_df.index, y=test_df["ypred"], mode='lines', name="Model",row=1, col=1)
fig.add_scatter(x=test_df.index, y=test_df["resids"], mode='lines', name="Residual (%)", row=1, col=2)
fig.update_layout(width=1000, height=500, title_text=f"{currency} and model, {title}")
fig.update_layout(showlegend=True)
fig.show()

print(pd.DataFrame(non_zero_coefficients,index=xvars).sort_values(by=0).round(2))

COP
Mean squared error: 11979.7
R-squared: 0.95


                    0
Japan          -14.75
Colombia       -12.87
Poland         -10.65
South Korea     -9.86
Peru            -6.18
United States   -5.70
Norway          -5.69
Brazil          -4.63
China           -2.98
Chile           -0.76
Canada          -0.41
Switzerland      0.38
Indonesia        0.42
France           1.06
Germany          1.29
United Kingdom   2.45
Mexico           2.95
India            3.55
Turkey           3.73
Sweden           5.66
Taiwan           5.87
Hong Kong        6.49
New Zealand      6.56
Australia        7.99
South Africa     8.45


0
Japan          -14.8
Colombia       -12.9
Poland         -10.6
South Korea     -9.9
Peru            -6.2
United States   -5.7
Norway          -5.7
Brazil          -4.6
China           -3.0
Chile           -0.8
Canada          -0.4
Switzerland      0.4
Indonesia        0.4
France           1.1
Germany          1.3
United Kingdom   2.4
Mexico           3.0
India            3.6
Turkey           3.7
Sweden           5.7
Taiwan           5.9
Hong Kong        6.5
New Zealand      6.6
Australia        8.0
South Africa     8.5